In [1]:
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'

In [2]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import torch.optim as optim
from torchtext.vocab import GloVe
from torchtext.data import Field, BucketIterator
from torchtext.data.metrics import bleu_score
import spacy
from nltk.translate.bleu_score import sentence_bleu, corpus_bleu

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [4]:
#Reading files

with open('trainen.txt', encoding='utf8') as f:
    eng_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('trainta.txt', encoding='utf8') as f:
    tamil_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('testen.txt', encoding='utf8') as f:
    eng_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('testta.txt', encoding='utf8') as f:
    tamil_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
embedding_glove = GloVe(name='6B', dim=100)

spacy_en = spacy.load('en_core_web_sm')

def tokenize_en(text):
    return [tok.text for tok in spacy_en.tokenizer(text)]

stop_words = [',','.','?','!',')','(',':',']','[','$','#','&','%','--']
ENG = Field(tokenize = tokenize_en, init_token='sos', eos_token = 'eos', lower=True, stop_words=stop_words)
processed_eng_train = list(map(lambda x: ENG.preprocess(x), eng_train))
processed_eng_test = list(map(lambda x: ENG.preprocess(x), eng_test))

ENG.build_vocab(processed_eng_train, vectors=embedding_glove)

In [5]:
def preprocess(processed_eng):
    
    #function to return the numericalized version of the tokenized sentences
    X = []
    for tokenized_sentence in processed_eng:
        int_sequence = [2]  #first element is the SOS token 
        for token in tokenized_sentence:
            int_sequence.append(ENG.vocab.stoi[token])
        int_sequence.append(3) #last element is the EOS token
        X.append(int_sequence)
    
    return X

# X_train and X_test are lists of lists with the integer sequences for a given sentence
X_train = preprocess(processed_eng_train)
X_test = preprocess(processed_eng_test)

In [6]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

# Same thing for Tamil sentences
TAM = Tokenizer()
TAM.fit_on_texts(tamil_train)
Y_train = TAM.texts_to_sequences(tamil_train)
Y_test = TAM.texts_to_sequences(tamil_test)

#adding EOS token
_ = [y.append(0) for y in Y_train]
_ = [y.append(0) for y in Y_test]

Using TensorFlow backend.


In [7]:
TAM.index_word[0] = 'EOS'
TAM.index_word[len(TAM.index_word)] = 'SOS'

In [8]:
source_vocab_size = len(ENG.vocab)
target_vocab_size = len(TAM.index_word)
print(source_vocab_size)
print(target_vocab_size)

9723
18670


In [9]:
# loading pretrained weights from numpy file
tamil_embedding = np.load('tam_embed.npy')
tamil_embedding = torch.from_numpy(tamil_embedding)

In [10]:
class Encoder(nn.Module):
    
    def __init__(self, embed_size, hidden_size, ENG):
        
        super(Encoder, self).__init__()
        self.embed_size = embed_size
        self.hidden_size = hidden_size
        self.embed = nn.Embedding.from_pretrained(ENG.vocab.vectors)
        self.lstm = nn.LSTM(embed_size, hidden_size)
        
    def forward(self, x, enc_hidden):
        
        embedded_x = self.embed(x)  # Ts x 100
        enc_output, enc_hidden = self.lstm(embedded_x.unsqueeze(1), enc_hidden)
        return enc_output, enc_hidden

In [11]:
class AttnDecoder(nn.Module):
    
    def __init__(self, hidden_size, n_classes, embeddings):
        
        super(AttnDecoder, self).__init__()
        self.embed_size = embeddings.shape[1]
        self.hidden_size = hidden_size
        self.embed = nn.Embedding.from_pretrained(embeddings)
        self.lstm = nn.LSTM(embeddings.shape[1] + hidden_size, hidden_size)
        self.fc = nn.Linear(hidden_size, n_classes)
        self.logsoftmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden, enc_hidden_states):
        
        # hidden is a tuple with each element of size 1,1,self.hidden_size
        # enc_hidden_states is of size Ts, self.hidden_size (Ts is the source length)
        embedded = self.embed(input).view(1, 1, -1)   # size is 1,1,self.embed_size
        
        #attn_scores will be of shape Ts
        attn_scores = torch.mm(enc_hidden_states, hidden[0].squeeze().view(-1,1)).squeeze()

        attn_weights = F.softmax(attn_scores, dim=0)
        
        # context will be of shape 1,1,self.hidden_size
        context = torch.bmm(attn_weights.view(1,1,-1), enc_hidden_states.unsqueeze(0))
        
        # new_input will be of shape 1,self.hidden_size + self.embed_size
        new_input = torch.cat((embedded[0], context[0]), 1)
        
        output, hidden = self.lstm(new_input.unsqueeze(0), hidden)

        output = self.logsoftmax(self.fc(output[0]))
        
        return output, hidden

In [12]:
def loss_per_pair(source_sentence, target_sentence, enc_obj, dec_obj, enc_optimiser, dec_optimiser, loss_fn):
    
    Ts = source_sentence.size(-1)
    Tt = target_sentence.size(-1)
    enc_hidden = (torch.zeros(1, 1, enc_obj.hidden_size, device=device), torch.zeros(1, 1, enc_obj.hidden_size, device=device))
    
    enc_optimiser.zero_grad()
    dec_optimiser.zero_grad()
    
    loss_val = 0
    
    enc_output, enc_hidden = enc_obj(source_sentence, enc_hidden) # enc_output will be Ts x 1 x hidden_size
        
    dec_input = torch.tensor([[target_vocab_size-1]], device=device)  #SOS token
    
    dec_hidden = enc_hidden
    
    for i in range(Tt):
        dec_output, dec_hidden = dec_obj(dec_input, dec_hidden, enc_output.squeeze(1))
        #_ , index = dec_output.topk(1)
        #dec_input = index.squeeze().detach()
        
        target_word = torch.cuda.LongTensor([target_sentence[i].item()])
        dec_input = target_word
        
        loss_val += loss_fn(dec_output, target_word)
        
        if dec_input.item() == 0:
            break

    loss_val.backward()
    
    nn.utils.clip_grad_norm_(enc_obj.parameters(), 0.5)
    nn.utils.clip_grad_norm_(dec_obj.parameters(), 0.5)

    enc_optimiser.step()
    dec_optimiser.step()

    return loss_val.item()/Tt

In [13]:
def train_model(sources, targets, enc_obj, dec_obj):
    
    loss_fn = nn.NLLLoss()
#     enc_optimiser = optim.SGD(enc_obj.parameters(), lr=0.0001, momentum=0.9)
#     dec_optimiser = optim.SGD(dec_obj.parameters(), lr=0.0001, momentum=0.9)
    enc_optimiser = optim.Adam(enc_obj.parameters())
    dec_optimiser = optim.Adam(dec_obj.parameters())
    
    max_epochs = 200
    old_loss = np.inf
    indices = [i for i in range(len(sources))]
    
    for epoch in range(max_epochs):
        
        # shuffling the input data manually at the start of every new epoch
        np.random.shuffle(indices)
        sources = list(np.array(sources)[indices])
        targets = list(np.array(targets)[indices])
        
        running_loss = 0.0
        num_sentences = len(sources)
        
        for i in range(num_sentences):
            source_sentence = torch.cuda.LongTensor(sources[i])
            target_sentence = torch.cuda.LongTensor(targets[i])

            loss = loss_per_pair(source_sentence, target_sentence, enc_obj, dec_obj, enc_optimiser, dec_optimiser, loss_fn)
            running_loss += loss

            if i%int(num_sentences*0.1)==0:
                print("Epoch", epoch+1, ":", (i/int(num_sentences*0.1))*10,'% done')
                print("Current loss:", running_loss)
                
        print('\nEpoch', epoch+1,"\n")
        print("Encoder obj lstm wts sum=", torch.sum(enc_obj.lstm.weight_ih_l0))
        print("Encoder obj lstm bias sum=", torch.sum(enc_obj.lstm.bias_ih_l0))
        print('Decoder obj emb wts sum=', torch.sum(dec_obj.embed.weight.data))
        print('Decoder obj lstm wts sum=', torch.sum(dec_obj.lstm.weight_ih_l0.data))
        print('Decoder obj lstm bias sum=', torch.sum(dec_obj.lstm.bias_ih_l0.data))
        print('Decoder obj linear wts sum=', torch.sum(dec_obj.fc.weight.data))
        print('Decoder obj linear bias sum=', torch.sum(dec_obj.fc.bias.data))
        
        if abs(running_loss-old_loss)/running_loss < 1e-4:
            print('Converged')
            break
    
        old_loss = running_loss

    print("Finished Training")

In [13]:
embedding_size = 100
hidden_size = 150
encoder = Encoder(embedding_size, hidden_size, ENG).to(device)
decoder = AttnDecoder(hidden_size, target_vocab_size, tamil_embedding).to(device)
#train_model(X_train, Y_train, encoder, decoder)

In [14]:
encoder.load_state_dict(torch.load('q4_encoder_weights.pt'))
decoder.load_state_dict(torch.load('q4_decoder_weights.pt'))

<All keys matched successfully>

In [16]:
torch.save(encoder.state_dict(), 'q4_encoder_weights.pt')
torch.save(decoder.state_dict(), 'q4_decoder_weights.pt')

In [31]:
def test_loss(sources, targets, enc_obj, dec_obj):
    
    loss_fn = nn.NLLLoss()
    num_sentences = len(sources)
    total_loss = 0
        
    for i in range(num_sentences):

        with torch.no_grad():

            source_sentence = torch.cuda.LongTensor(sources[i])
            target_sentence = torch.cuda.LongTensor(targets[i])
            Ts = source_sentence.size(-1)
            Tt = target_sentence.size(-1)
            enc_hidden = (torch.zeros(1, 1, enc_obj.hidden_size, device=device), torch.zeros(1, 1, enc_obj.hidden_size, device=device))
            
            loss_val = 0
            
            enc_output, enc_hidden = enc_obj(source_sentence, enc_hidden)

            dec_input = torch.tensor([[target_vocab_size-1]], device=device)  #SOS token

            # first hidden state of decoder is made the final hidden state of the encoder
            dec_hidden = enc_hidden
            

            for j in range(Tt):

                dec_output, dec_hidden = dec_obj(dec_input, dec_hidden, enc_output.squeeze(1))
                _ , index = dec_output.topk(1)
                dec_input = index.squeeze().detach()
                if index.item() == 0:
                    break

                target_word = torch.cuda.LongTensor([target_sentence[j].item()])

                loss_val += loss_fn(dec_output, target_word)
            
            total_loss += loss_val.item()/Tt
    
    return total_loss

In [32]:
# this test loss is for 500 sentences
test_loss(X_test, Y_test, encoder, decoder)

AttributeError: 'int' object has no attribute 'item'

In [15]:
def eval_bleu(enc_obj, dec_obj, source_sentence, target, target_vocab_dict):
    
    # function to return the BLEU score for a single sentence 
    
    with torch.no_grad():
        
        Ts = source_sentence.size(-1)
        enc_hidden = (torch.zeros(1, 1, enc_obj.hidden_size, device=device), torch.zeros(1, 1, enc_obj.hidden_size, device=device))
    
        enc_output, enc_hidden = enc_obj(source_sentence, enc_hidden)
    
        dec_input = torch.tensor([[target_vocab_size-1]], device=device)  # SOS

        dec_hidden = enc_hidden
        predicted = []

        for i in range(60):
            dec_output, dec_hidden = dec_obj(dec_input, dec_hidden, enc_output.squeeze(1))
            _ , index = dec_output.data.topk(1)
            if index.item() == 0:
                #decoded_words.append('<EOS>')
                break
            else:
                predicted.append(target_vocab_dict[index.item()])

            dec_input = index.squeeze().detach()
            
    target = [target]
    
    print("Predicted:",predicted)
    print("Target:",target)
    
    return predicted, target

In [16]:
def evaluate_model(enc_obj, dec_obj, source_test, target_test, target_vocab_dict):
    
    # returns the average bleu score for the model with the given test data
    
    n = len(source_test)
    all_pred = []
    all_targets = []
    for i in range(n):
        source_sentence = torch.cuda.LongTensor(source_test[i])
        target = [target_vocab_dict[x] for x in target_test[i][:-1]]
        pred, trg = eval_bleu(enc_obj, dec_obj, source_sentence, target, target_vocab_dict)
        all_pred.append(pred)
        all_targets.append(trg)
        
    
    corp_bleu1 = corpus_bleu(all_targets, all_pred, weights=(1.0, 0, 0, 0))
    corp_bleu2 = corpus_bleu(all_targets, all_pred, weights=(0.5, 0.5, 0, 0))
    corp_bleu3 = corpus_bleu(all_targets, all_pred, weights=(1/3, 1/3, 1/3, 0))
    corp_bleu4 = corpus_bleu(all_targets, all_pred)
    
    return corp_bleu1, corp_bleu2, corp_bleu3, corp_bleu4

In [30]:
evaluate_model(encoder, decoder, X_train, Y_train, TAM.index_word)

Predicted: ['நாம்', 'எங்கே', 'போகிறோம்', 'என்று']
Target: [['நாம்', 'எங்கே', 'போகிறோம்', 'என்று']]
Predicted: ['அவர்கள்', 'terraforming']
Target: [['அவர்கள்', 'terraforming']]
Predicted: ['நீங்கள்', 'சார்லஸ்டன்', 'என்னை', 'கிடைக்கும்', 'துடைக்க', 'வேண்டும்']
Target: [['நீங்கள்', 'சார்லஸ்டன்', 'என்னை', 'கிடைக்கும்', 'துடைக்க', 'வேண்டும்']]
Predicted: ['இல்லை', 'அவர்', 'என்', 'அப்பா', 'இல்லை']
Target: [['இல்லை', 'அவர்', 'என்', 'அப்பா', 'இல்லை']]
Predicted: ['நான்', 'ஞாயிறுகளில்', 'அவளை', 'எங்கே', 'இருந்தேன்']
Target: [['நான்', 'ஞாயிறுகளில்', 'அவளை', 'நாம்', 'மற்ற', 'கூறினார்']]
Predicted: ['ஒடிஸி', 'பொறியியல்']
Target: [['கோள்களின்', 'பொறியியல்']]
Predicted: ['90', 'சதவிகிதம்', 'தானாம்', 'dr', 'brand']
Target: [['90', 'சதவிகிதம்', 'தானாம்', 'dr', 'brand']]
Predicted: ['இந்த', 'அனுப்பினார்']
Target: [['இந்த', 'அனுப்பினார்']]
Predicted: ['அது']
Target: [['அது']]
Predicted: ['நான்', 'யோசிக்காமல்', 'விளையாட்டுகளில்', 'நான்']
Target: [['நான்', 'யோசிக்காமல்', 'விளையாட்டுகளில்', 'அதிகம

Predicted: ['நான்', 'தேவாலயத்தில்', 'போகிறேன்']
Target: [['நான்', 'தேவாலயத்தில்', 'போகிறேன்']]
Predicted: ['இலவச', 'கையில்']
Target: [['இலவச', 'கையில்']]
Predicted: ['உன்கூட', 'இருந்துட்டு', 'அரை', 'மணி', 'நேரத்துக்கு', 'அப்புறம்']
Target: [['உன்கூட', 'இருந்துட்டு', 'அரை', 'மணி', 'நேரத்துக்கு', 'அப்புறம்']]
Predicted: ['கடைசியா', 'நான்', 'வெறும்', 'ஒன்னு', 'வேலைய', 'கண்டுபிடுச்சுட்டேன்', 'எனக்கேத்த']
Target: [['கடைசியா', 'நான்', 'ஒரு', 'வேலைய', 'கண்டுபிடுச்சுட்டேன்', 'எனக்கேத்த', 'மாதிரியா', 'ஒன்றை']]
Predicted: ['வணக்கம்', 'அம்மா', 'இதுகேண்டிஉள்ளது']
Target: [['வணக்கம்', 'அம்மா', 'இதுகேண்டிஉள்ளது']]
Predicted: ['யாரு', 'இந்த', 'அழகு', 'நான்', 'எடுத்துக்குறே']
Target: [['யாரு', 'இந்த', 'அழகு', 'நான்', 'எடுத்துக்குறே']]
Predicted: ['murph', 'சீக்கிரம்', 'சீக்கிரம்']
Target: [['murph', 'சீக்கிரம்', 'வா']]
Predicted: ['கூட']
Target: [['கூட']]
Predicted: ['எனவே', 'நீங்கள்', 'இதை', 'என்ன', 'கண்டுபிடிக்க']
Target: [['ஏன்', 'நீங்கள்', 'இதை', 'இருக்கும்']]
Predicted: ['யே', 'இல்ல', 'மன்னிச்ச

Predicted: ['ஒவ்வொரு', 'முறையும்', 'ஒவ்வொரு', 'உங்கள்', 'பெயரை', 'குறிப்பிடுகிறார்']
Target: [['ஒவ்வொரு', 'முறையும்', 'யாரோ', 'உங்கள்', 'பெயரை', 'குறிப்பிடுகிறார்']]
Predicted: ['ஒரு', 'உணர்வு']
Target: [['ஒரு', 'உணர்வு']]
Predicted: ['அந்த', 'பையன்']
Target: [['அந்த', 'பையன்', 'தவிர']]
Predicted: ['நான்']
Target: [['நான்']]
Predicted: ['அவர்கள்', 'நாட்டின்', 'தண்டிக்க', 'முடிவு']
Target: [['அவர்கள்', 'நாட்டின்', 'தண்டிக்க', 'முடிவு']]
Predicted: ['இந்த', 'பாடல்', 'சில', 'சூடான', 'ஆடைகள்', 'செய்யவும்']
Target: [['இந்த', 'பாடல்', 'சில', 'சூடான', 'ஆடைகள்', 'செய்யவும்']]
Predicted: ['மக்கள்எங்களைஅதே']
Target: [['மக்கள்எங்களைஅதே']]
Predicted: ['நீங்கள்', 'இதை', 'செய்ய', 'ஏதாவது', 'செய்ய', 'வேண்டும்']
Target: [['இத', 'வெச்சு', 'எதாவது', 'பண்ணனுமா']]
Predicted: ['இந்த', 'எடு']
Target: [['இந்த', 'எடு']]
Predicted: ['இல்லை', 'அது', 'தொலயல']
Target: [['இல்லை', 'அது', 'தொலயல']]
Predicted: ['தோலையொட்டிய', 'அதை', 'நிறுத்து']
Target: [['தோலையொட்டிய', 'அதை', 'நிறுத்து']]
Predicted: ['நாம', '

Predicted: ['அவன்', 'தனது', 'பக்க', 'மைல்கள்', 'அவர்', 'அவளை', 'வெளியே', 'உள்ளது']
Target: [['அவர்', 'அவரது', 'பணப்பையை', 'திருடி', 'அதை', 'திரும்பி', 'வருகிறார்', 'இல்லை']]
Predicted: ['இது', 'செல்லம்', 'நீ', 'தான்']
Target: [['இது', 'செல்லம்', 'நீ', 'தான்']]
Predicted: ['அவர்களை', 'கொட்டு', 'ஆனால்', 'மிகவும்', 'இன்னும்', 'இல்லை', 'இல்லையா']
Target: [['அவர்களை', 'கொட்டு', 'விட', 'மிகவும்', 'அல்ல', 'நீங்கள்', 'என்று', 'இல்லை']]
Predicted: ['மெடிக்காகவும்பணியாற்றிவந்தார்']
Target: [['மெடிக்காகவும்பணியாற்றிவந்தார்']]
Predicted: ['ஆஸ்பத்திரிக்கு', 'போகலாம்']
Target: [['ஆஸ்பத்திரிக்கு', 'போகலாம்']]
Predicted: ['5', 'கிராண்ட்', 'மதிப்பு', 'விலை', 'தான்', 'இன்னொரு', '100', 'ரூபாய்', 'கடைசி', 'முறை', 'பதிவு']
Target: [['5', 'கிராண்ட்', 'மதிப்பு', 'என்', 'ஜன்னலை', 'கொடுக்க', 'முடியாது']]
Predicted: ['கூட்டு', 'ஒன்று', 'செயல்படுத்தவும்']
Target: [['கூட்டு', 'ஒன்று', 'செயல்படுத்தவும்']]
Predicted: ['தாயார்', 'நீங்கள்', 'இன்னும்', 'போல்']
Target: [['தாயார்', 'உனக்கு', 'இன்னும்', 'நேரம்', 'இட

Predicted: ['இதை', 'செய்கிறேன்', 'வேண்டாம்']
Target: [['நான்', 'சில', 'recon', 'செய்ய', 'வரை', 'எதையும்', 'நடத்த', 'வேண்டாம்']]
Predicted: ['இது', 'நடக்கிறது']
Target: [['இது', 'நடக்கிறது']]
Predicted: ['ரோன்னி', 'நான்', 'என்னை', 'தனது', 'அடைய', 'குறைந்தபட்சம்', 'உங்கள்', 'இரண்டு', 'ஜன்னல்', 'கொடுக்க', 'கொடுக்க', 'கொடுக்க', 'ஒரு', 'டன்', 'திட்டத்தை', 'திட்டத்தை', 'அடைய', 'ஒரு', 'சலுகை', 'கிடைத்தது']
Target: [['ரோன்னி', 'எனக்கு', 'ஒரு', 'கிக்', 'பேக்', 'எறிந்து', 'கேச்ட்', 'தனது', 'கடன்கள்', 'மீது', 'வட்டி', 'கொள்ளும்', 'வட்டி', 'இருந்து', 'என்னுடைய', 'நிலுவையில்', 'உள்ள', 'வரி', 'விவகாரங்களை', 'முடிக்க']]
Predicted: ['நீ', 'என்னை']
Target: [['உனக்கு', 'என்னை', 'தொட', 'வேண்டும்']]
Predicted: ['என்று', 'அடுத்த', 'நீங்கள்', 'வேண்டும்', 'என்றால்', 'நான்', 'நம்புகிறேன்']
Target: [['மற்றும்', 'ஒருவேளை', 'நீங்கள்', 'இயக்க', 'வேண்டும்', 'நான்', '25', 'என்று']]
Predicted: ['நான்', 'நான்', 'உங்களுக்கு', 'ஏனெனில்', 'ஏன்', 'இந்த', 'போகிறேன்']
Target: [['நான்', 'நான்', 'உங்களுக்கு', 'ஏனெனில்', 

...

Predicted: ['ஒரு', 'கதை', 'கொடுக்கிறது']
Target: [['ஒரு', 'கதை', 'கொடுக்கிறது']]
Predicted: ['அலெக்ஸ்']
Target: [['அலெக்ஸ்']]
Predicted: ['நான்', 'அனைத்து', 'முன்னர்', 'இருக்கிறேன்', 'நினைக்கிறேன்']
Target: [['நான்', 'பிறகு', 'தவறு', 'இல்லை', 'என்று', 'நினைக்கிறேன்']]
Predicted: ['சரி', 'துருப்புக்கள்', 'வா', 'ம்']
Target: [['வலது', 'துருப்புக்கள்', 'வா', 'போகலாம்']]
Predicted: ['அதுனால', 'நானும்', 'உன்ன', 'கேட்குறேன்']
Target: [['அதுனால', 'நானும்', 'உன்ன', 'கேட்குறேன்']]
Predicted: ['நான்', 'இனி', 'கவனம்', 'செய்து']
Target: [['நான்', 'சரி', 'வெளியே', 'இருக்கும்', 'போலீஸ்', 'சொல்']]
Predicted: ['போதும்', 'ஜூடித்']
Target: [['போதும்', 'ஜூடித்']]
Predicted: ['அதுல', 'லஞ்சம்', 'வாங்க', 'கூடாதுன்னு', 'சொல்லுது']
Target: [['அதுல', 'லஞ்சம்', 'வாங்க', 'கூடாதுன்னு', 'சொல்லுது']]
Predicted: ['நல்லது', 'அது', 'மோசமான', 'எடுப்பாய்', 'இருக்கிறது']
Target: [['நல்லது', 'அது', 'மோசமான', 'எடுப்பாய்', 'இருக்கிறது']]
Predicted: ['அதாவது']
Target: [['அதாவது']]
Predicted: ['அமைதியாய்', 'இரு']
Tar

Predicted: ['நீங்கள்', 'யாரிடமும்']
Target: [['நீங்கள்', 'யாரிடமும்']]
Predicted: ['நான்', 'இரண்டு', 'யு', 'ஆல்', 'வாண்ட்', 'இன்', 'dicks', 'குடித்தார்கள்']
Target: [['நான்', 'இரண்டு', 'யு', 'ஆல்', 'வாண்ட்', 'இன்', 'dicks', 'குடித்தார்கள்']]
Predicted: ['எல்லாம்', 'திரும்ப', 'விரும்பினால்']
Target: [['எல்லாம்', 'மீண்டும்', 'அது', 'வழி', 'செல்ல', 'முடியும்']]
Predicted: ['சர்']
Target: [['சார்']]
Predicted: ['ஒவ்வொருத்தருக்கும்', 'அவங்க', 'வழி', 'இஸ்தார்']
Target: [['ஒவ்வொருத்தருக்கும்', 'அவங்க', 'அவங்க', 'வழி', 'இஸ்தார்']]
Predicted: ['நான்', 'அம்மா', 'இருக்க', 'முடியாது']
Target: [['நான்', 'அம்மா', 'இருக்க', 'முடியாது']]
Predicted: ['சரி', 'எங்கள்', 'திட்டம்', 'எங்களுக்கு', 'தான்']
Target: [['சரி', 'பிறகு', 'எங்கள்', 'இலக்கு', 'அல்ல']]
Predicted: ['சர்']
Target: [['சர்']]
Predicted: ['நான்', 'இங்கே', 'இருக்கிறேன்']
Target: [['நான்', 'இங்கு', 'தான்', 'உள்ளேன்']]
Predicted: ['நாம்']
Target: [['நாங்கள்']]
Predicted: ['என்று', 'தொகை', 'பிச்', 'பார்த்துக்கொள்ளுங்கள்']
Target: [['என்று', 

Predicted: ['இருநூற்றி', 'எண்பத்தி', 'நான்கு', 'பதில்']
Target: [['இருநூற்றி', 'எண்பத்தி', 'நான்கு', 'அதற்கு', 'பதில்']]
Predicted: ['நாம்']
Target: [['நாம்']]
Predicted: ['நீங்கள்', 'இன்னும்', 'வேண்டும்']
Target: [['நமக்கு', 'இன்னும்', 'அதிகம்', 'தேவைப்பட்டது']]
Predicted: ['நான்', 'பார்க்க', 'என்ன', 'பார்க்க', 'வேண்டாம்']
Target: [['நான்', 'பார்க்க', 'என்ன', 'நம்ப', 'முடியவில்லை']]
Predicted: ['நாம்', 'இறந்த', 'தொடர்பு', 'உள்ளன']
Target: [['நாம்', 'முன்பே', 'இறந்திருப்போம்']]
Predicted: ['நான்', 'போய்', 'இல்லை', 'என்றால்']
Target: [['நான்', 'போய்', 'இல்லை', 'என்றால்']]
Predicted: ['திரிய', 'மற்றும்', 'ஆண்கள்', 'மற்றும்', 'பெண்கள்', 'கலப்பது']
Target: [['திரிய', 'மற்றும்', 'ஆண்கள்', 'மற்றும்', 'பெண்கள்', 'கலப்பது']]
Predicted: ['நான்', 'இப்போது', 'உங்களுக்கு', 'சில', 'உடைக்க', 'முடியும்', 'காரணம்']
Target: [['நான்', 'இப்போது', 'உங்களுக்கு', 'சில', 'விண்வெளி', 'கொடுக்க', 'செல்கிறேன்']]
Predicted: ['case', '500', 'மீட்டர்']
Target: [['case', '500', 'மீட்டர்']]
Predicted: ['அவளை', 

Predicted: ['நீங்கள்', 'எப்போதும்', 'அதை', 'பார்க்க', 'வேண்டும்']
Target: [['நீ', 'ஒரு', 'வாய்ப்ப', 'பார்த்திருக்க', 'அதோடு', 'நீ', 'ஓடு']]
Predicted: ['அவர்', 'ஒரு', 'நீண்ட', 'வாழ்வு', 'ஒரு', 'நீண்ட', 'அதை', 'கண்டுபிடிக்க', 'முடியாது']
Target: [['இன்னும்', 'அவனால்', 'இசைக்க', 'முடியும்', 'யாரும்', 'அவன', 'விரும்புறதில்ல']]
Predicted: ['நான்', 'கற்று', 'முடியும்']
Target: [['நான்', 'கற்று', 'கொள்ள', 'முடியும்']]
Predicted: ['பூமி', 'போர்முன்']
Target: [['பூமி', 'போர்முன்']]
Predicted: ['எடுப்பாய்', 'இல்லை']
Target: [['எடுப்பாய்', 'இல்லை']]
Predicted: ['78', 'ரோம்லே', 'அவென்யு', 'மே']
Target: [['78', 'ரோம்லே', 'அவென்யு', 'மே']]
Predicted: ['என்ன', 'ஒருவனுடன்', 'பிறகு', 'தான்']
Target: [['என்ன', 'ஒருவனுடன்', 'நடந்தது']]
Predicted: ['ஆமா', 'உண்மை']
Target: [['ஆமா', 'உண்மை']]
Predicted: ['நான்', 'ஹே', 'மோசமாக', 'இன்று', 'வரை', 'ஸ்க்ரீவ்டு']
Target: [['நான்', 'ஹே', 'மோசமாக', 'இன்று', 'வரை', 'ஸ்க்ரீவ்டு']]
Predicted: ['யாரோ', 'என்ன', 'விளையாடுகிறீர்களா']
Target: [['யாருக்காவது', 'அடி'

(0.6718042675960816,
 0.5780271296427701,
 0.4905312860432136,
 0.39918640393056176)

In [17]:
evaluate_model(encoder, decoder, X_test, Y_test, TAM.index_word)

Predicted: ['ஆனால்', 'இரண்டு', 'மில்லியன்', 'விட', 'என்', 'பணம்']
Target: [['s', 'i', 's', 'மூன்று', 'வயது', 'நடுத்தர', 'ஊதியம்', 'கடந்த', 'மூன்று', 'ஆண்டுகளில்']]
Predicted: ['நீ', 'ஒரு', 'தேர்வு', 'செய்ய', 'வேண்டும்']
Target: [['நீங்கள்', 'தேர்வு', 'செய்ய', 'வேண்டும்']]
Predicted: ['நீங்கள்', 'உங்கள்', 'பிச்', 'உங்கள்', 'பிச்', 'எங்கே', 'நீங்கள்', 'outta']
Target: [['பிட்ச்', 'நீங்கள்', 'நல்ல', 'உங்கள்', 'என்', 'என்', 'அலுவலக', 'outta']]
Predicted: ['நீங்கள்', 'இதை', 'பேசுவேன்']
Target: [['மற்றும்', 'உலக', 'எங்களை', 'பற்றி', 'மறக்க', 'முடியாது']]
Predicted: ['என்', 'செல்', 'மற்றும்', 'உன்', 'வேலைய']
Target: [['என்', 'செல்', 'போன்', 'மூலம்']]
Predicted: ['இந்த', 'மற்ற', 'அதிகாரி', 'யின்', 'மீது', 'அடைய', 'நம்மை', 'மூலம்', 'சென்றது']
Target: [['இந்த', 'சாரணர்', 'கப்பல்', 'இருந்தது', 'வெற்றிடத்தை', 'ஆயிரக்கணக்கான', 'ஒன்றாகும்']]
Predicted: ['மற்றும்', 'ஒரு', 'கடத்தல்காரர்', 'தான்', 'ஒரு', 'சிறிய', 'மனிதன்', 'என்னை', 'ஒரு', 'போர்வீரன்']
Target: [['பெண்', 'பாடல்', 'இருண்ட', 'மற்றும்', '

Predicted: ['அவளுக்கு', 'உள்ளே', 'வர', 'இருக்கு', 'நான்', 'உங்க', 'வேலை', 'முன்']
Target: [['நம்பு', 'அல்லது', 'நான்', 'முன்', 'கதவு', 'வழியாக', 'வந்தது', 'இல்லை']]
Predicted: ['நான்', 'ஒன்றும்', 'உணவு', 'சாப்பிட', 'வேண்டும்']
Target: [['நான்', 'ஒரு', 'வீட்டில்', 'சமைத்த', 'உணவை', 'சாப்பிட', 'வேண்டும்']]
Predicted: ['உங்கள்', 'திரும்பி', 'இரவு', 'வரை', 'நாம்', 'ஒப்பிட்டு', 'வேண்டும்']
Target: [['அவர்கள்', 'நான்', 'உங்கள்', 'இடது', 'பக்கத்தில்', 'உள்ள', 'வசிக்கிறார்கள்', 'வருகிறேன்']]
Predicted: ['சரி', 'உங்கள்', 'கழுதை', 'கண்டுபிடித்து', 'வரை', 'ஒருமுறை', 'நீங்கள்', 'போன்ற', 'போல்', 'எவ்வாறு', 'உள்ளது']
Target: [['சரி', 'நீங்கள்', 'ஒரு', 'சிறிய', 'மகன்', 'உதவுகிறது', 'ஆனால்', 'நீங்கள்', 'பிரச்சனையில்', 'இன்னும்']]
Predicted: ['நீ', 'ஒரு', 'பார்க்க', 'பார்க்க', 'பார்க்க']
Target: [['நீங்கள்', 'உங்களை', 'பார்க்க', 'ஒரு']]
Predicted: ['சரி', 'லிசா', 'அவரது', 'பாப்டிஸ்ட்', 'ஒரு', 'சார்ஜென்ட்', 'கவனமா']
Target: [['பெயர்', 'என்று', 'சரி', 'மார்கஸ்', 'பாப்டிஸ்ட்']]
Predicted: ['ஓ', 'நீங்கள்

Predicted: ['நான்', 'கேட்டு', 'நான்', 'எப்போதும்', 'இருக்கிறேன்']
Target: [['நான்', 'நான்', 'இங்கே', 'முன்', 'இருந்தது', 'என்று', 'கற்பனை']]
Predicted: ['அவரது', 'புதிய', 'பக்கத்தில்', 'நாம்', 'அவரது', 'வேலை', 'கடைசி', 'பயணத்தை', 'வேலை', 'இல்லை']
Target: [['நம்மளோட', 'இழப்பு', 'அவனுக்கு', 'பதிய', 'முதலாளி', 'நல்ல', 'ஒரு', 'முன்னேற்றம்']]
Predicted: ['பைத்தியம்', 'ஒன்றும்', 'இந்த', 'காரணம்', 'ஒன்றும்', 'இருக்கிறது']
Target: [['வெற்றி', 'எடுத்து', 'கொண்டு', 'ஒன்றும்', 'தவறு', 'இல்லை']]
Predicted: ['என்', 'சந்தை', 'உள்ளது']
Target: [['எனது', 'தொலைபேசி', 'ஸ்டில்', 'in', 'உள்ளது']]
Predicted: ['நான்', 'அவர்கள்', 'அழ', 'இப்போது', 'பார்க்க', 'முடியாது']
Target: [['நான்', 'அவர்களுக்கு', 'கல்', 'பாதிக்கப்படுகின்றனர்', 'செய்ய', 'போகிறேன்']]
Predicted: ['ஆனால்', 'நான்', 'நான்', 'அவரை', 'பார்த்தேன்', 'போறேன்']
Target: [['ஆனால்', 'நான்', 'நான்', 'என்று', 'நான்', 'அவரை', 'பார்த்தேன்']]
Predicted: ['இந்த', 'மோசமா', 'மோசமா', 'உன்னை', 'விட', 'போன்ற', 'மலிவான']
Target: [['பெரும்பாலான', 'குற்றவாளிக

Predicted: ['அங்கே', 'என்னுடைய', 'கதை', 'யாரும்', 'சொல்ல', 'கடனாளி', 'பகுதியில்']
Target: [['தான்', 'வெளியே', 'உலக', 'ஒரு', 'மாறாக', 'மோசமான', 'என்று', 'நாம்']]
Predicted: ['இது', 'திரும்ப', 'அவளை', 'திரும்ப', 'விட', 'என்', 'ரொம்ப', 'ஒரு', 'சில', 'சொல்றேன்']
Target: [['என்', 'அப்படியே', 'விட்டுவிட்டு', 'ஒரு']]
Predicted: ['நீ', 'உங்கள்', 'திரும்ப', 'திரும்ப', 'பெற', 'முடியும்']
Target: [['பிறகு', 'நீங்கள்', 'உங்கள்', 'திரும்பி', 'செல்ல', 'முடியும்']]
Predicted: ['நீங்கள்', 'இன்று', 'இன்று', 'இன்று', 'பொது', 'கோரிக்கை', 'தொடங்க', 'வேண்டும்']
Target: [['நீங்கள்', 'தேவாலயத்தில்', 'இங்கே', 'சில', 'ஏற்க', 'வேண்டும்', 'என்று']]
Predicted: ['நீ', 'உங்கள்', 'பாதுகாப்பு', 'வாழ்க்கையை', 'மாற்ற', 'முடியும்']
Target: [['உங்கள்', 'வாழ்க்கை', 'மாற்ற', 'மற்றும்', 'நகர்த்த']]
Predicted: ['ஆம்', 'இப்போது', 'wckd', 'மைல்', 'என்று', 'ஒரு', 'நிமிடம்', 'அல்ல', 'இன்னும்']
Target: [['இல்லை', 'பரிந்துரை', 'மிகவும்', 'கடினமாக', 'இருக்கிறது', 'நிலை']]
Predicted: ['இந்த', 'இந்த', 'கதை', 'என்', 'முகத்தை', 'ந

Predicted: ['வா', 'நீ', 'போய்', 'ஒரு', 'இன்னும்', 'கொஞ்சம்', 'வேலை', 'கண்டுபிடிக்க', 'வேலை', 'சரியா']
Target: [['நாம்', 'ஒரு', 'பேச்சு', 'உட்கார்', 'வேண்டும்', 'எதிர்கால', 'தயார்']]
Predicted: ['நீங்கள்', 'உயிருடன்', 'பார்த்தால்', 'நாம்', 'இறந்து', 'விடுவேன்']
Target: [['உங்களுக்கு', 'பதில்', 'நாம்', 'தனியாக', 'இருக்கிறாயா']]
Predicted: ['நீங்கள்', "'கோயிங்", 'யு', 'ஆல்', 'வாண்ட்', 'செய்து', 'துடைக்க', 'வேண்டும்']
Target: [['நீ', 'எனக்காக', 'அனைத்து', 'சாம்பல்', 'முடி', 'மற்றும்', 'பெறுகின்றனர்']]
Predicted: ['நான்', 'பிரமை', 'நீங்கள்', 'அவரை', 'வெறுக்கிறேன்']
Target: [['நான்', 'அவர்கள்', 'பிரமை', 'என்னை', 'அனுப்பினார்', 'நினைவில்']]
Predicted: ['இது', 'மிகவும்', 'புணர்கிறேன்', 'என', 'உள்ளது']
Target: [['இந்த', 'புணர்கிறேன்', 'அமெரிக்க', 'கனவு', 'யு', 'ஆல்', 'வாண்ட்', 'உள்ளது']]
Predicted: ['நாம்', 'ஒருவருக்கொருவர்', 'ஒருவருக்கொருவர்', 'நிறைய', 'பயன்படுத்தப்படும்']
Target: [['நாம்', 'இருவரும்', 'ஒருவரை', 'ஒருவர்', 'கவர்ந்து', 'இல்லை']]
Predicted: ['நீங்கள்', 'professor', 'போலவே', '

...

Predicted: ['டாக்டர்', 'ஜாயே', 'தொடர்பு', 'என்றார்', 'விசாரணை', 'ஐந்து', 'வழக்கறிஞர்', 'வழக்கறிஞர்', 'என்றார்']
Target: [['ராபர்ட்', 'brogden', 'எங்கள்', 'அப்பா', 'அவரை', 'முன்', 'இரண்டு', 'தசாப்தங்களாக', 'இருந்தது', 'ஷெரிப்']]
Predicted: ['மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மேற்கு', 'மாளிகை', 'முன்', 'விலகினார்', 'இருந்தது']
Target: [['தென்', 'கொரிய', 'அதிகாரிகள்', 'இப்போது', 'அவர்கள்', 'என்று', 'சொல்கிறீர்கள்', 'மற்றும்', 'அவர்கள்', 'பதில்', 'கூடுதல்', 'அலகுகள்', 'வருகிறது']]
Predicted: ['சிலபேர்', 'அவனோட', 'அவனோட', 'சிறிய', 'நேரம்', 'ஆமா', 'ஆமா', 'அவனோட', 'சொல்லு']
Target: [['உடைந்த', 'மக்களின்', 'முழு', 'ஒரு', 'உள்ள', 'ல்', 'நான்']]
Predicted: ['இல்லை', 'நான்', 'வெறும்', 'ஆண்டுகள்', 'இரண்டு', 'வருடம்', 'மூன்று', 'முறை', 'இதனை']
Target: [['இல்லை', 'ஆனால்', 'நான்', 'பி', 'எம்', 'விற்றேன்', 'நான்கு', 'வாரங்களுக்கு', 'முன்', 'என்று', 'நினைவிருக்கிறது']]
Predicted: ['பெற

Predicted: ['மூன்று', 'துண்டுகள்', 'நீங்கள்', 'எல்லாவற்றையும்', 'உங்கள்', 'நினைவுகள்', 'என்று', 'உங்கள்', 'நினைவுகள்', 'என்று', 'உங்கள்', 'நினைவுகள்', 'எனவே', 'உங்கள்', 'தந்தை', 'அல்லது', 'இந்த', 'வாழ்நாள்', 'எப்படி']
Target: [['உலக', 'போர்', 'உண்மையில்', 'இந்த', 'எரிபொருள்', 'வழங்கும்', 'நீங்கள்', 'ஹிட்லர்', 'போராட', 'வெளிநாட்டு', 'செல்லும்', 'போது', 'அந்த', 'நீங்கள்', 'உங்கள்', 'நண்பர்களுடன்', 'கொல்லப்பட்டனர்', 'பார்க்க']]
Predicted: ['என்', 'ஜன்னல்', 'வந்தவர்களில்', 'என்', 'ஜன்னல்', 'ஜன்னல்', 'மற்றும்', 'ஜன்னல்', 'ஆனால்', 'என்', 'பிட்டர்', 'மற்றும்', 'குழந்தைகளை', 'செல்', 'மற்றும்', 'மீண்டும்', 'ஆனால்', 'தனியார்', 'ஜன்னல்', 'மற்றும்', 'இணைய', 'குறிப்பு', 'என்', 'வாழ்க்கையில்', 'சுற்றி', 'வருகிறோம்', 'வேண்டும்', 'என்', 'வீட்டை', 'விட்டு']
Target: [['என்னுடைய', 'அக்கம்', 'என்', 'வீட்டு', 'படுக்கை', 'சில', 'சத்தம்', 'புகார்', 'நீங்க', 'வந்து', 'என்', 'இருந்து', 'சத்தம்', 'வெளியே', 'போறத', 'சரி', 'செய்யனும்']]
Predicted: ['நான்', 'அத', 'நானே', 'நீங்க', 'இருங்க', 'கிட்ட', 'சொல்றே',

Predicted: ['நாங்கள்', 'கமாண்டர்', 'ஆண்டுகளாக', 'பாதுகாப்பாக', 'இரண்டு', 'வருடங்கள்', 'பாதுகாப்பாக', 'உள்ள', 'இரண்டு', 'வாரங்களுக்கு', 'உள்ள', 'உங்கள்', 'சிகிச்சை', 'உள்ள', 'படை', 'உள்ளது', 'ஐந்து', 'நேர', 'இருக்கிறது']
Target: [['இல்லை', 'நீங்கள்', 'தான்', 'சமீபத்திய', 'இருக்கிறீர்கள்', 'என்', 'அப்களை', 'ஒரு', 'நீண்ட', 'வரிசையில்', 'ஒரு', 'இந்த', 'நிறுவனம்', 'திரும்பி', 'அரசியல்', 'மற்றும்', 'சிறப்பு', 'ஆயுதங்கள்', 'சார்பில்', 'மற்றும்', 'கண்காணிப்பு', 'துறை']]
Predicted: ['நான்', 'இங்கே', 'தான்', 'என்', 'இருந்தாலும்', 'என்னால', 'காரணம்', 'ரோன்னீ', 'என்பது', 'ஆனால்', 'அதனால', 'அந்த', 'நல்லா', 'பிட்ஸ்பாட்ரிக்', 'விரும்புறேன்']
Target: [['நான்', 'அந்த', 'மக்கள்', 'ஒரு', 'என்று', 'நினைத்தது', 'இல்லை', 'என்று', 'பிறந்த', 'நாள்', 'ஆனால்', 'அதை', 'நான்', 'இருக்க', 'விரும்பவில்லை', 'நான்', 'இல்லை', 'என்று', 'ஒரு', 'நினைவூட்டல்', 'என்று', 'உணர்கிறார்']]
Predicted: ['அந்த', 'தெரியாது', 'அந்த', 'ஆள்', 'உனக்கு', 'தெரியாது', 'தெரியாது', 'நீங்கள்', 'இருந்து', 'போன்ற', 'அந்த', 'தெரியாது', 'குழந்தை

Predicted: ['மற்றும்', 'அவர்', 'சமீபத்தில்', 'இருந்து', 'போது', 'அவர்', 'உன்', 'தந்தை', 'திட்டம்', 'ஆனால்', 'அவர்', 'பணத்தை', 'உணர', 'முடியவில்லை', 'ஆனால்', 'அவர்', 'ஒரு', 'உணர்வு', 'திட்டம்', 'வரும்', 'போது', 'அவர்', 'வாழ்க்கை', 'வரும்', 'போது', 'அவர்', 'குடும்பத்தை', 'வரும்']
Target: [['அவர்', 'அந்த', 'வார்த்தை', 'பேசும்', 'போது', 'உங்கள்', 'என்ற', 'மிக', 'சொந்த', 'உலக', 'வந்தவர்', 'அதில்', 'இருந்து', 'ஒரே', 'அவர்', 'நீங்கள்', 'திரும்ப', 'கொண்டு', 'வர', 'முடியும்']]
Predicted: ['மூன்று', 'துண்டுகள்', 'நீங்கள்', 'எல்லாவற்றையும்', 'உங்கள்', 'நினைவுகள்', 'என்று', 'உங்கள்', 'நினைவுகள்', 'என்று', 'உங்கள்', 'நினைவுகள்', 'எனவே', 'உங்கள்', 'தந்தை', 'அல்லது', 'இந்த', 'வாழ்நாள்', 'எப்படி']
Target: [['உலக', 'போர்', 'உண்மையில்', 'இந்த', 'எரிபொருள்', 'வழங்கும்', 'நீங்கள்', 'ஹிட்லர்', 'போராட', 'வெளிநாட்டு', 'செல்லும்', 'போது', 'அந்த', 'நீங்கள்', 'உங்கள்', 'நண்பர்களுடன்', 'கொல்லப்பட்டனர்', 'பார்க்க']]
Predicted: ['நான்', 'அவர்களின்', 'பொருட்களை', 'fucking', 'ஏனெனில்', 'நான்', 'அவளை', 'த

(0.15265944877626333,
 0.05089840360759847,
 0.020547360575992202,
 0.011031872521985292)